We have data from different sources:
* [x] ATLAS: **2048** labeled images
    * BCC
    * BKL
    * DF
    * MEL: **252**    
    * NV
    * VASC
    * MISC -> none of above
* [x] EXTERNAL: **1327** labeled images
    * AKIEC
    * ANV
    * BCC
    * DF
    * MEL: **103**
    * SCC
* [x] ISIC2019: **25331** labeled images, 8240 unlabeled images
    * AKIEC
    * BCC
    * BKL
    * DF
    * NV
    * VASC
    * SCC
    * MEL: **4522**
    * MISC -> none of the above
* [x] LUMC: **463** labeled images, 4 classes
    * MEL: **142**
    * ANV (looks similar to MEL but is actually innocent)
    * NV
    * MISC -> none of the above
* [x] SD198: **6981** labeled images, 198 classes
    * MEL: **115** (ignore the VB images!)
    * NOTE: train with small center-crop (25\%)
* [x] MEDNODE: **170** labeled images, 2 classes
    * MEL: 70 
    * NV: 100    
* [] PH2: **200** labeled images, 3 classes
    * MEL: 40
    * NV: 80
    * ANV: 80
* [x] ISIC2020: **33126** labeled images, 10982 unlabeled images
    * MEL: **584**
    * NV
    * BKL: seborrheic keratosis, lichenoid keratosis, lentigo NOS, cafe-au-lait macule, solar lentigo
    * ANV: atypical melanocytic proliferation
    * MISC: -> none of the above
    
So in total we have about **68813** labeled images, **5576** of which are from melanoma.

Our goal is to train a classifier on the classes in the ISIC2020 competition, these 
are simply: melanoma/other.

Literature suggests that all-versus-all classifiers generalise better than one-versus all classifier, 
hence it makes sense to pre-train base classifiers on the historical data on all the classes all-v-all.

To prepare the data for our purposes we want to structure it as follows:
```
train\
    class_0
    class_1
    ..
```
and we want the data frame containing the targets to look like
```
image_id, class_0, class_1...
```

We will create that structure in this notebook.

In [1]:
import os
import sys
import pandas as pd
import shutil
from tqdm import tqdm

In [2]:
os.chdir('/media/bramiozo/DATA-FAST/kaggle/image_classification/MEDICAL')

# ATLAS

In [6]:
df_atlas = pd.read_csv('melanoma/ATLAS/atlas_derm_meta.csv')

In [13]:
def cp_file(src, dst):
    try:
        shutil.copy(src, dst)
        return True
    except IOError as e:
        print(e)
        return False
    
def create_target_subdir(input_class_list, target_dir):
    try:
        os.mkdir(target_dir)
    except OSError as e:
        print(e)

    for c in input_class_list:
        try:
            c_dir = "{}{}/".format(target_dir, c)

            os.mkdir(c_dir)
        except OSError as e:
            print(e)

def cp_file_to_class_folder(path_label_tuple, base_path, target_path):    
    label, path = path_label_tuple
    try:
        cp_file(base_path + path, target_path + str(label))
    except TypeError as e:
        print(e)

In [26]:
create_target_subdir(df_atlas.superclass.unique().tolist(), 'melanoma/ATLAS/train/')

for _t in tqdm(df_atlas[['superclass', 'clinic', 'derm']].itertuples()):
    _class = _t[1]
    _loc1 = _t[2]
    _loc2 = _t[3]
    cp_file_to_class_folder((_class, _loc1), 'melanoma/ATLAS/images/', 'melanoma/ATLAS/train/')
    cp_file_to_class_folder((_class, _loc2), 'melanoma/ATLAS/images/', 'melanoma/ATLAS/train/')

136it [00:00, 1355.86it/s]

[Errno 17] File exists: 'melanoma/ATLAS/train/'
[Errno 17] File exists: 'melanoma/ATLAS/train/bcc/'
[Errno 17] File exists: 'melanoma/ATLAS/train/nv/'
[Errno 17] File exists: 'melanoma/ATLAS/train/df/'
[Errno 17] File exists: 'melanoma/ATLAS/train/misc/'
[Errno 17] File exists: 'melanoma/ATLAS/train/mel/'
[Errno 17] File exists: 'melanoma/ATLAS/train/bkl/'
[Errno 17] File exists: 'melanoma/ATLAS/train/vasc/'


1011it [00:00, 1398.99it/s]


# ISIC2019

In [18]:
df_isic2019 = pd.read_csv('melanoma/ISIC2019/ISIC_2019_Training_GroundTruth.csv')

In [25]:
keys = {0: 'mel', 1: 'nv', 2: 'bcc', 3: 'akiec', 4: 'bkl', 5: 'df', 6: 'vasc', 7: 'scc', 8: 'misc'}
def get_class(x):
    for k, v in x.items():
        if v == 1:
            return k.lower()
    
df_isic2019['class'] = df_isic2019[['MEL', 'NV', 'BCC', 'AK', 'BKL', 'DF', 'VASC', 'SCC', 'UNK']].\
                            apply(lambda x: get_class(x), axis=1)
df_isic2019.drop(['MEL', 'NV', 'BCC', 'AK', 'BKL', 'DF', 'VASC', 'SCC', 'UNK'], axis=1, inplace=True)
df_isic2019['loc'] = df_isic2019['image'].apply(lambda x: x+'.jpg')

In [30]:
create_target_subdir(df_isic2019['class'].unique().tolist(), 'melanoma/ISIC2019/train/')

for _t in tqdm(df_isic2019[['class', 'loc']].itertuples()):
    _class = _t[1]
    _loc = _t[2]
    cp_file_to_class_folder((_class, _loc), 
                            'melanoma/ISIC2019/training_images/', 
                            'melanoma/ISIC2019/train/')

261it [00:00, 2606.06it/s]

[Errno 17] File exists: 'melanoma/ISIC2019/train/'


25331it [00:18, 1402.92it/s]


# LUMC

In [37]:
df_lumc = pd.read_csv('melanoma/LUMC/train_metadata.csv')
df_lumc['Bestand'] = df_lumc.Bestandsnummer.apply(lambda x: str(x)+'.jpg')
create_target_subdir(df_lumc['Diagnose'].unique().tolist(), 'melanoma/LUMC/train/')


In [22]:
for _t in tqdm(df_lumc[['Diagnose', 'Bestand']].itertuples()):
    _class = _t[1]
    _loc = str(_t[2])
    try:
        cp_file_to_class_folder((_class, _loc), 
                                'melanoma/LUMC/images/', 
                                'melanoma/LUMC/train/')
    except:
        pass

NameError: name 'df_lumc' is not defined

# Check overlap ISIC2020 with ISIC2019

In [49]:
df_isic2019 = pd.read_csv('melanoma/ISIC2019/ISIC_2019_Training_GroundTruth.csv')
df_isic2020_test = pd.read_csv('melanoma/ISIC2020/siim-isic-melanoma-classification/test.csv')
df_isic2020 = pd.read_csv('melanoma/ISIC2020/siim-isic-melanoma-classification/train.csv')

In [50]:
isic2020 = set(df_isic2020.image_name.tolist())
isic2020_test = set(df_isic2020_test.image_name.tolist())
isic2019 = set(df_isic2019.image.tolist())

overlap_train = isic2019.intersection(isic2020)
overlap_test = isic2019.intersection(isic2020_test)

No overlap in image identifiers..

# ISIC2020

In [3]:
df_isic2020 = pd.read_csv('melanoma/ISIC2020/siim-isic-melanoma-classification/train.csv')

In [5]:
class_map = {'unknown': 'misc',
             'melanoma': 'mel',
             'seborrheic keratosis': 'bkl',
             'lichenoid keratosis': 'bkl',
             'lentigo NOS': 'bkl',
             'cafe-au-lait macule': 'bkl',
             'solar lentigo': 'bkl',
             'nevus': 'nv',
             'atypical melanocytic proliferation': 'anv'}

df_isic2020['class']  =  df_isic2020.diagnosis.map(class_map)
df_isic2020['loc'] = df_isic2020['image_name'].apply(lambda x: x+'.jpg')

In [15]:
create_target_subdir(df_isic2020['class'].unique().tolist(), 'melanoma/ISIC2020/train/')
for _t in tqdm(df_isic2020[['class', 'loc']].itertuples()):
    _class = _t[1]
    _loc = _t[2]
    cp_file_to_class_folder((_class, _loc), 'melanoma/ISIC2020/siim-isic-melanoma-classification/jpeg/train/', 
                            'melanoma/ISIC2020/train/')

74it [00:00, 729.24it/s]

[Errno 17] File exists: 'melanoma/ISIC2020/train/'
[Errno 17] File exists: 'melanoma/ISIC2020/train/misc/'
[Errno 17] File exists: 'melanoma/ISIC2020/train/nv/'
[Errno 17] File exists: 'melanoma/ISIC2020/train/mel/'
[Errno 17] File exists: 'melanoma/ISIC2020/train/bkl/'
[Errno 17] File exists: 'melanoma/ISIC2020/train/anv/'


33126it [00:47, 690.59it/s] 


# PH2

In [37]:
df_ph2 = pd.read_csv('melanoma/tmp/PH2Dataset/PH2.csv', sep=';')

In [38]:
sdir='melanoma/tmp/PH2Dataset/'

In [39]:
df_ph2['image_pathname'] = df_ph2['Image Name'].apply(lambda x: 'source/'+x+'/'+x+'_Dermoscopic_Image/'+x+'.bmp')
df_ph2['segment_pathname'] = df_ph2['Image Name'].apply(lambda x: 'source/'+x+'/'+x+'_lesion/'+x+'_lesion.bmp')
df_ph2['segment_special1_pathname'] = df_ph2['Image Name'].apply(lambda x: 'source/'+x+'/'+x+'_roi/'+x+'_R1_Label4.bmp')
df_ph2['segment_special2_pathname'] = df_ph2['Image Name'].apply(lambda x: 'source/'+x+'/'+x+'_roi/'+x+'_R2_Label3.bmp')

In [42]:
# write to folders
# 
for _t in tqdm(df_ph2[['class', 'image_pathname']].itertuples()):
    _class = _t[1]
    _loc = _t[2]
    cp_file_to_class_folder((_class, _loc), sdir, sdir+'train/')


200it [00:00, 924.39it/s]


## Cropped images

In [7]:
images = pd.read_csv("melanoma/TRAINING_1024/meta_enriched.csv", sep=";")

In [20]:
image_path = "melanoma/TRAINING_200_crop/TRAIN/"

In [21]:
create_target_subdir(images['target_new'].unique().tolist(), image_path)

[Errno 17] File exists: 'melanoma/TRAINING_200_crop/TRAIN/'


In [23]:
# write to folders
# 
for _t in tqdm(images[['target_new', 'filename']].itertuples()):
    _class = _t[1]
    _loc = _t[2]
    try:
        cp_file_to_class_folder((_class, _loc), image_path, image_path)
    except:
        pass

920it [00:00, 4412.21it/s]

[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000000.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000001.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000002.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000003.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000004.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000006.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000007.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000008.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000009.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000010.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0000011.jpg'
[Errno 2] No such fil

2004it [00:00, 4880.26it/s]


[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010264.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010265.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010267.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010317.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010318.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010319.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010320.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010321.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010322.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010323.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_0010326.jpg'
[Errno 2] No such fi

3171it [00:00, 5338.89it/s]

...

[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7362188.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7363391.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7363483.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7365628.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7366427.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7367079.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7367641.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7367817.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7369674.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7371368.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_7372476.jpg'
[Errno 2] No such fil

77112it [00:15, 6193.97it/s]

[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8544337.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8544906.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8546598.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8546808.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8549378.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8551002.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8551580.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8553381.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8553859.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8554769.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_8556045.jpg'
[Errno 2] No such fil

78139it [00:15, 5145.99it/s]

[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9677559.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9677935.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9679360.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9681414.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9681634.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9684090.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9684470.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9685490.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9685762.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9686337.jpg'
[Errno 2] No such file or directory: 'melanoma/TRAINING_200_crop/TRAIN/ISIC_9687740.jpg'
[Errno 2] No such fil